# Pose Error Project
### (Transformer-Encoder)

In [1]:
import logging

logging.basicConfig(format='%(asctime)s | %(levelname)s : %(message)s', level=logging.INFO)
logger = logging.getLogger(__name__)

logger.info("Loading packages ...")
import os
import sys
import time
import pickle
import json

# 3rd party packages

#from tqdm import tqdm
# since we are using it in jupyter notebook
from tqdm.notebook import tqdm

import torch
from torch.utils.data import DataLoader
from torch.utils.tensorboard import SummaryWriter

# Project modules
from options import Options
from running import setup, pipeline_factory, validate, check_progress, NEG_METRICS
from utils import utils
from datasets.data import data_factory, Normalizer
from datasets.datasplit import split_dataset
from models.ts_transformer import model_factory
from models.loss import get_loss_module
from optimizers import get_optimizer

import parser


2023-05-11 13:51:40,903 | INFO : Loading packages ...
2023-05-11 13:51:42,170 | INFO : Note: NumExpr detected 32 cores but "NUMEXPR_MAX_THREADS" not set, so enforcing safe limit of 8.
2023-05-11 13:51:42,170 | INFO : NumExpr defaulting to 8 threads.


# Setup Configurations

In [2]:
# Setting 1 - Single Stage
# Training From Scratch
text = "--output_dir ../experiments/ --comment 'poseErrorPred_from_Scratch' \
        --name poseErrorPred_fromScratch_Regression_Selective --records_file Regression_records.xls \
        --data_dir ../data/SenseTimeV4_Selective/ --data_class pose \
        --epochs 50 --lr 0.0001 --optimizer RAdam --batch_size 128 \
        --pos_encoding learnable --task regression --print_interval 1"

In [3]:
# Setting 2 - Two Stages
# Pretrain
'''
text = "--output_dir ../experiments/ --comment 'pretraining_through_imputation' \
        --name pm25_pretrained --records_file Imputation_records.xls \
        --data_dir ../data/regression/BeijingPM25Quality/ --data_class tsra \
        --pattern TRAIN --val_ratio 0.2 --epochs 20 --lr 0.001 --optimizer RAdam \
        --batch_size 32 --pos_encoding learnable --d_model 128"
'''

# Finetune
'''
text = "--output_dir ../experiments --comment 'finetune_for_regression' \
        --name BeijingPM25Quality_finetuned --records_file Regression_records.xls \
        --data_dir ../data/regression/BeijingPM25Quality/ --data_class tsra \
        --pattern TRAIN --val_pattern TEST  --epochs 100 --lr 0.001 --optimizer RAdam \
        --pos_encoding learnable --d_model 128 \
        --load_model ../experiments/pm25_pretrained_2023-05-04_11-01-18_AhP/checkpoints/model_best.pth \
        --task regression --change_output --batch_size 128"
'''

'\ntext = "--output_dir ../experiments --comment \'finetune_for_regression\'         --name BeijingPM25Quality_finetuned --records_file Regression_records.xls         --data_dir ../data/regression/BeijingPM25Quality/ --data_class tsra         --pattern TRAIN --val_pattern TEST  --epochs 100 --lr 0.001 --optimizer RAdam         --pos_encoding learnable --d_model 128         --load_model ../experiments/pm25_pretrained_2023-05-04_11-01-18_AhP/checkpoints/model_best.pth         --task regression --change_output --batch_size 128"\n'

In [4]:
# Process the setting string
# Generate the config variable
input_text = text.split()
args = Options().parse(input_text)
config = setup(args)

2023-05-11 13:51:42,306 | INFO : Stored configuration file in '../experiments/poseErrorPred_fromScratch_Regression_Selective_2023-05-11_13-51-42_STl'


In [5]:
config

{'config_filepath': None,
 'output_dir': '../experiments/poseErrorPred_fromScratch_Regression_Selective_2023-05-11_13-51-42_STl',
 'data_dir': '../data/SenseTimeV4_Selective/',
 'load_model': None,
 'resume': False,
 'change_output': False,
 'save_all': False,
 'experiment_name': 'poseErrorPred_fromScratch_Regression_Selective',
 'comment': "'poseErrorPred_from_Scratch'",
 'no_timestamp': False,
 'records_file': 'Regression_records.xls',
 'console': False,
 'print_interval': 1,
 'gpu': '0',
 'n_proc': -1,
 'num_workers': 0,
 'seed': None,
 'limit_size': None,
 'test_only': None,
 'data_class': 'pose',
 'labels': None,
 'test_from': None,
 'test_ratio': 0,
 'val_ratio': 0.2,
 'pattern': None,
 'val_pattern': None,
 'test_pattern': None,
 'normalization': 'standardization',
 'norm_from': None,
 'subsample_factor': None,
 'task': 'regression',
 'masking_ratio': 0.15,
 'mean_mask_length': 3,
 'mask_mode': 'separate',
 'mask_distribution': 'geometric',
 'exclude_feats': None,
 'mask_feats':

# Setup Logger

In [6]:
# Add file logging besides stdout
file_handler = logging.FileHandler(os.path.join(config['output_dir'], 'output.log'))
logger.addHandler(file_handler)

logger.info('Running:\n{}\n'.format(' '.join(sys.argv)))  # command used to run

2023-05-11 13:51:42,465 | INFO : Running:
/home/tianyi/anaconda3/envs/transformer/lib/python3.8/site-packages/ipykernel_launcher.py -f /home/tianyi/.local/share/jupyter/runtime/kernel-9e773c25-08a6-4d58-8e6b-8c05ee5483db.json



# Setup Training Device

In [7]:
if config['seed'] is not None:
    torch.manual_seed(config['seed'])

device = torch.device('cuda' if (torch.cuda.is_available() and config['gpu'] != '-1') else 'cpu')
logger.info("Using device: {}".format(device))
if device == 'cuda':
    logger.info("Device index: {}".format(torch.cuda.current_device()))

2023-05-11 13:51:43,411 | INFO : Using device: cuda


# Prepare Data

In [8]:
 # Build data
logger.info("Loading and preprocessing data ...")
data_class = data_factory[config['data_class']]
my_data = data_class(config['data_dir'], 
                     pattern=config['pattern'], 
                     n_proc=config['n_proc'], 
                     limit_size=config['limit_size'], 
                     config=config)
feat_dim = my_data.feature_df.shape[1]  # dimensionality of data features
if config['task'] == 'classification':
    validation_method = 'StratifiedShuffleSplit'
    labels = my_data.labels_df.values.flatten()
else:
    validation_method = 'ShuffleSplit'
    labels = None
    
# Modify for the pose error pred
validation_method = 'PoseErrorTimeSplit'

2023-05-11 13:51:43,986 | INFO : Loading and preprocessing data ...
2023-05-11 13:51:43,988 | INFO : Loading 69 datasets files using 32 parallel processes ...


In [9]:
feat_dim = my_data.feature_df.shape[1]
feat_dim

12

In [10]:
my_data.feature_df
#my_data.all_IDs[0:50]

brightness   entropy  num_images  min_corners  min_keypoints  \
index                                                                        
100000100000    0.558603  7.294162       104.0       1478.0         1001.0   
100000100000    0.558561  7.291242       104.0       1478.0         1001.0   
100000100000    0.559005  7.288196       103.0       1478.0         1001.0   
100000100000    0.558873  7.285532       103.0       1478.0         1001.0   
100000100000    0.559256  7.282616       102.0       1478.0         1001.0   
...                  ...       ...         ...          ...            ...   
100701001729    0.509410  7.456340       181.0       1644.0         1001.0   
100701001729    0.509763  7.455523       180.0       1644.0         1001.0   
100701001729    0.510118  7.454677       179.0       1644.0         1001.0   
100701001729    0.510464  7.453780       178.0       1644.0         1001.0   
100701001729    0.510811  7.452860       177.0       1644.0         1001.0   

              max_keypoints_diff  min_keypoint_dist  min_inliers  \
index                                                              
100000100000                 7.0               0.99         51.0   
100000100000                 7.0               0.99         51.0   
100000100000                 7.0               0.99         51.0   
100000100000                 7.0               0.99         51.0   
100000100000                 7.0               0.99         51.0   
...                          ...                ...          ...   
100701001729                 7.0               0.98        257.0   
100701001729                 7.0               0.98        257.0   
100701001729                 7.0               0.98        257.0   
100701001729                 7.0               0.98        257.0   
100701001729                 7.0               0.98        257.0   

              localba_error  localba_visual_error  localba_inertial_error  \
index                                                                       
100000100000    6178.850098           8706.259766               42.412201   
100000100000    6178.850098           8706.259766               42.412201   
100000100000    6178.850098           8706.259766               42.412201   
100000100000    6178.850098           8706.259766               42.412201   
100000100000    6178.850098           8706.259766               42.412201   
...                     ...                   ...                     ...   
100701001729   24245.800781          26154.699219              175.932007   
100701001729   24245.800781          26154.699219              175.932007   
100701001729   24245.800781          26154.699219              175.932007   
100701001729   24245.800781          26154.699219              175.932007   
100701001729   24245.800781          26154.699219              175.932007   

              acc_magnitude  
index                        
100000100000      14.840897  
100000100000       9.759345  
100000100000       9.757799  
100000100000       9.753009  
100000100000       9.753572  
...                     ...  
100701001729       9.718341  
100701001729       9.718509  
100701001729       9.718246  
100701001729       9.717584  
100701001729       9.717959  

[5303040 rows x 12 columns]

In [11]:
type(my_data.labels_df)

pandas.core.frame.DataFrame

In [12]:
my_data.labels_df.values

array([[0.06220907],
       [0.06657413],
       [0.06772166],
       ...,
       [0.0063161 ],
       [0.0063301 ],
       [0.00633432]], dtype=float32)

In [13]:
5916480/123260

48.0

In [14]:
#from datasets import utils
#x, y = utils.load_from_tsfile_to_dataframe("../data/regression/BeijingPM25Quality/BeijingPM25Quality_TRAIN.ts")
#y.shape
#x

In [15]:
my_data.labels_df.shape

(110480, 1)

In [16]:
total_epoch_time = 0
total_eval_time = 0

total_start_time = time.time()

# Split dataset

In [17]:
# Split dataset
test_data = my_data
test_indices = None  # will be converted to empty list in `split_dataset`, if also test_set_ratio == 0
val_data = my_data
val_indices = []
if config['test_pattern']:  # used if test data come from different files / file patterns
    test_data = data_class(config['data_dir'], pattern=config['test_pattern'], n_proc=-1, config=config)
    test_indices = test_data.all_IDs
if config['test_from']:  # load test IDs directly from file, if available, otherwise use `test_set_ratio`. Can work together with `test_pattern`
    test_indices = list(set([line.rstrip() for line in open(config['test_from']).readlines()]))
    try:
        test_indices = [int(ind) for ind in test_indices]  # integer indices
    except ValueError:
        pass  # in case indices are non-integers
    logger.info("Loaded {} test IDs from file: '{}'".format(len(test_indices), config['test_from']))
if config['val_pattern']:  # used if val data come from different files / file patterns
    val_data = data_class(config['data_dir'], pattern=config['val_pattern'], n_proc=-1, config=config)
    val_indices = val_data.all_IDs

In [18]:
config

{'config_filepath': None,
 'output_dir': '../experiments/poseErrorPred_fromScratch_Regression_Selective_2023-05-11_13-51-42_STl',
 'data_dir': '../data/SenseTimeV4_Selective/',
 'load_model': None,
 'resume': False,
 'change_output': False,
 'save_all': False,
 'experiment_name': 'poseErrorPred_fromScratch_Regression_Selective',
 'comment': "'poseErrorPred_from_Scratch'",
 'no_timestamp': False,
 'records_file': 'Regression_records.xls',
 'console': False,
 'print_interval': 1,
 'gpu': '0',
 'n_proc': -1,
 'num_workers': 0,
 'seed': None,
 'limit_size': None,
 'test_only': None,
 'data_class': 'pose',
 'labels': None,
 'test_from': None,
 'test_ratio': 0,
 'val_ratio': 0.2,
 'pattern': None,
 'val_pattern': None,
 'test_pattern': None,
 'normalization': 'standardization',
 'norm_from': None,
 'subsample_factor': None,
 'task': 'regression',
 'masking_ratio': 0.15,
 'mean_mask_length': 3,
 'mask_mode': 'separate',
 'mask_distribution': 'geometric',
 'exclude_feats': None,
 'mask_feats':

In [19]:
config['test_from']

In [20]:
str(10200300).split('0')

['1', '2', '', '3', '', '']

In [21]:
config['val_pattern']

In [22]:
validation_method

'PoseErrorTimeSplit'

In [23]:
# Note: currently a validation set must exist, either with `val_pattern` or `val_ratio`
# Using a `val_pattern` means that `val_ratio` == 0 and `test_ratio` == 0
if config['val_ratio'] > 0:
    train_indices, val_indices, test_indices = split_dataset(data_indices=my_data.all_IDs,
                                                             validation_method=validation_method,
                                                             n_splits=1,
                                                             validation_ratio=config['val_ratio'],
                                                             test_set_ratio=config['test_ratio'],  # used only if test_indices not explicitly specified
                                                             test_indices=test_indices,
                                                             random_seed=1337,
                                                             labels=labels)
    train_indices = train_indices[0]  # `split_dataset` returns a list of indices *per fold/split*
    val_indices = val_indices[0]  # `split_dataset` returns a list of indices *per fold/split*
else:
    train_indices = my_data.all_IDs
    if test_indices is None:
        test_indices = []

In [24]:
logger.info("{} samples may be used for training".format(len(train_indices)))
logger.info("{} samples will be used for validation".format(len(val_indices)))
logger.info("{} samples will be used for testing".format(len(test_indices)))

2023-05-11 13:52:05,138 | INFO : 88355 samples may be used for training
2023-05-11 13:52:05,139 | INFO : 22125 samples will be used for validation
2023-05-11 13:52:05,140 | INFO : 0 samples will be used for testing


In [25]:
with open(os.path.join(config['output_dir'], 'data_indices.json'), 'w') as f:
    try:
        json.dump({'train_indices': list(map(int, train_indices)),
                   'val_indices': list(map(int, val_indices)),
                   'test_indices': list(map(int, test_indices))}, f, indent=4)
    except ValueError:  # in case indices are non-integers
        json.dump({'train_indices': list(train_indices),
                   'val_indices': list(val_indices),
                   'test_indices': list(test_indices)}, f, indent=4)


In [26]:
# Pre-process features
normalizer = None
if config['norm_from']:
    with open(config['norm_from'], 'rb') as f:
        norm_dict = pickle.load(f)
    normalizer = Normalizer(**norm_dict)
elif config['normalization'] is not None:
    normalizer = Normalizer(config['normalization'])
    my_data.feature_df.loc[train_indices] = normalizer.normalize(my_data.feature_df.loc[train_indices])
    if not config['normalization'].startswith('per_sample'):
        # get normalizing values from training set and store for future use
        norm_dict = normalizer.__dict__
        with open(os.path.join(config['output_dir'], 'normalization.pickle'), 'wb') as f:
            pickle.dump(norm_dict, f, pickle.HIGHEST_PROTOCOL)
if normalizer is not None:
    if len(val_indices):
        val_data.feature_df.loc[val_indices] = normalizer.normalize(val_data.feature_df.loc[val_indices])
    if len(test_indices):
        test_data.feature_df.loc[test_indices] = normalizer.normalize(test_data.feature_df.loc[test_indices])


In [27]:
train_indices

[100000100000,
 100000100001,
 100000100002,
 100000100003,
 100000100004,
 100000100005,
 100000100006,
 100000100007,
 100000100008,
 100000100009,
 100000100010,
 100000100011,
 100000100012,
 100000100013,
 100000100014,
 100000100015,
 100000100016,
 100000100017,
 100000100018,
 100000100019,
 100000100020,
 100000100021,
 100000100022,
 100000100023,
 100000100024,
 100000100025,
 100000100026,
 100000100027,
 100000100028,
 100000100029,
 100000100030,
 100000100031,
 100000100032,
 100000100033,
 100000100034,
 100000100035,
 100000100036,
 100000100037,
 100000100038,
 100000100039,
 100000100040,
 100000100041,
 100000100042,
 100000100043,
 100000100044,
 100000100045,
 100000100046,
 100000100047,
 100000100048,
 100000100049,
 100000100050,
 100000100051,
 100000100052,
 100000100053,
 100000100054,
 100000100055,
 100000100056,
 100000100057,
 100000100058,
 100000100059,
 100000100060,
 100000100061,
 100000100062,
 100000100063,
 100000100064,
 100000100065,
 100000100

In [28]:
val_indices

[100000100800,
 100000100801,
 100000100802,
 100000100803,
 100000100804,
 100000100805,
 100000100806,
 100000100807,
 100000100808,
 100000100809,
 100000100810,
 100000100811,
 100000100812,
 100000100813,
 100000100814,
 100000100815,
 100000100816,
 100000100817,
 100000100818,
 100000100819,
 100000100820,
 100000100821,
 100000100822,
 100000100823,
 100000100824,
 100000100825,
 100000100826,
 100000100827,
 100000100828,
 100000100829,
 100000100830,
 100000100831,
 100000100832,
 100000100833,
 100000100834,
 100000100835,
 100000100836,
 100000100837,
 100000100838,
 100000100839,
 100000100840,
 100000100841,
 100000100842,
 100000100843,
 100000100844,
 100000100845,
 100000100846,
 100000100847,
 100000100848,
 100000100849,
 100000100850,
 100000100851,
 100000100852,
 100000100853,
 100000100854,
 100000100855,
 100000100856,
 100000100857,
 100000100858,
 100000100859,
 100000100860,
 100000100861,
 100000100862,
 100000100863,
 100000100864,
 100000100865,
 100000100

In [29]:
test_indices

[]

# Create model

In [30]:
# Create model
logger.info("Creating model ...")
model = model_factory(config, my_data)

if config['freeze']:
    for name, param in model.named_parameters():
        if name.startswith('output_layer'):
            param.requires_grad = True
        else:
            param.requires_grad = False

logger.info("Model:\n{}".format(model))
logger.info("Total number of parameters: {}".format(utils.count_parameters(model)))
logger.info("Trainable parameters: {}".format(utils.count_parameters(model, trainable=True)))


2023-05-11 13:52:11,727 | INFO : Creating model ...
2023-05-11 13:52:11,758 | INFO : Model:
TSTransformerEncoderClassiregressor(
  (project_inp): Linear(in_features=12, out_features=64, bias=True)
  (pos_enc): LearnablePositionalEncoding(
    (dropout): Dropout(p=0.1, inplace=False)
  )
  (transformer_encoder): TransformerEncoder(
    (layers): ModuleList(
      (0): TransformerBatchNormEncoderLayer(
        (self_attn): MultiheadAttention(
          (out_proj): NonDynamicallyQuantizableLinear(in_features=64, out_features=64, bias=True)
        )
        (linear1): Linear(in_features=64, out_features=256, bias=True)
        (dropout): Dropout(p=0.1, inplace=False)
        (linear2): Linear(in_features=256, out_features=64, bias=True)
        (norm1): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
        (norm2): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
        (dropout1): Dropout(p=0.1, inplace=False)
        (dro

# Initialize optimizer

In [31]:
# Initialize optimizer
if config['global_reg']:
    weight_decay = config['l2_reg']
    output_reg = None
else:
    weight_decay = 0
    output_reg = config['l2_reg']

optim_class = get_optimizer(config['optimizer'])
optimizer = optim_class(model.parameters(), lr=config['lr'], weight_decay=weight_decay)

start_epoch = 0
lr_step = 0  # current step index of `lr_step`
lr = config['lr']  # current learning step
# Load model and optimizer state
if args.load_model:
    model, optimizer, start_epoch = utils.load_model(model, config['load_model'], optimizer, config['resume'],
                                                     config['change_output'],
                                                     config['lr'],
                                                     config['lr_step'],
                                                     config['lr_factor'])
model.to(device)

loss_module = get_loss_module(config)

In [32]:
if config['test_only'] == 'testset':  # Only evaluate and skip training
    dataset_class, collate_fn, runner_class = pipeline_factory(config)
    test_dataset = dataset_class(test_data, test_indices)

    test_loader = DataLoader(dataset=test_dataset,
                             batch_size=config['batch_size'],
                             shuffle=False,
                             num_workers=config['num_workers'],
                             pin_memory=True,
                             collate_fn=lambda x: collate_fn(x, max_len=model.max_len))
    test_evaluator = runner_class(model, test_loader, device, loss_module,
                                        print_interval=config['print_interval'], console=config['console'])
    aggr_metrics_test, per_batch_test = test_evaluator.evaluate(keep_all=True)
    print_str = 'Test Summary: '
    for k, v in aggr_metrics_test.items():
        print_str += '{}: {:8f} | '.format(k, v)
    logger.info(print_str)
    #return

In [33]:
config

{'config_filepath': None,
 'output_dir': '../experiments/poseErrorPred_fromScratch_Regression_Selective_2023-05-11_13-51-42_STl',
 'data_dir': '../data/SenseTimeV4_Selective/',
 'load_model': None,
 'resume': False,
 'change_output': False,
 'save_all': False,
 'experiment_name': 'poseErrorPred_fromScratch_Regression_Selective',
 'comment': "'poseErrorPred_from_Scratch'",
 'no_timestamp': False,
 'records_file': 'Regression_records.xls',
 'console': False,
 'print_interval': 1,
 'gpu': '0',
 'n_proc': -1,
 'num_workers': 0,
 'seed': None,
 'limit_size': None,
 'test_only': None,
 'data_class': 'pose',
 'labels': None,
 'test_from': None,
 'test_ratio': 0,
 'val_ratio': 0.2,
 'pattern': None,
 'val_pattern': None,
 'test_pattern': None,
 'normalization': 'standardization',
 'norm_from': None,
 'subsample_factor': None,
 'task': 'regression',
 'masking_ratio': 0.15,
 'mean_mask_length': 3,
 'mask_mode': 'separate',
 'mask_distribution': 'geometric',
 'exclude_feats': None,
 'mask_feats':

In [34]:
# Initialize data generators
if config['test_only'] != 'testset':  # Only evaluate and skip training
    dataset_class, collate_fn, runner_class = pipeline_factory(config)
    val_dataset = dataset_class(val_data, val_indices)

    val_loader = DataLoader(dataset=val_dataset,
                            batch_size=config['batch_size'],
                            shuffle=False,
                            num_workers=config['num_workers'],
                            pin_memory=True,
                            collate_fn=lambda x: collate_fn(x, max_len=model.max_len))

    train_dataset = dataset_class(my_data, train_indices)

    train_loader = DataLoader(dataset=train_dataset,
                              batch_size=config['batch_size'],
                              shuffle=True,
                              num_workers=config['num_workers'],
                              pin_memory=True,
                              collate_fn=lambda x: collate_fn(x, max_len=model.max_len))

    trainer = runner_class(model, train_loader, device, loss_module, optimizer, l2_reg=output_reg,
                                 print_interval=config['print_interval'], console=config['console'])
    val_evaluator = runner_class(model, val_loader, device, loss_module,
                                       print_interval=config['print_interval'], console=config['console'])

    tensorboard_writer = SummaryWriter(config['tensorboard_dir'])

    best_value = 1e16 if config['key_metric'] in NEG_METRICS else -1e16  # initialize with +inf or -inf depending on key metric
    metrics = []  # (for validation) list of lists: for each epoch, stores metrics like loss, ...
    best_metrics = {}

[100000100800, 100000100801, 100000100802, 100000100803, 100000100804, 100000100805, 100000100806, 100000100807, 100000100808, 100000100809, 100000100810, 100000100811, 100000100812, 100000100813, 100000100814, 100000100815, 100000100816, 100000100817, 100000100818, 100000100819, 100000100820, 100000100821, 100000100822, 100000100823, 100000100824, 100000100825, 100000100826, 100000100827, 100000100828, 100000100829, 100000100830, 100000100831, 100000100832, 100000100833, 100000100834, 100000100835, 100000100836, 100000100837, 100000100838, 100000100839, 100000100840, 100000100841, 100000100842, 100000100843, 100000100844, 100000100845, 100000100846, 100000100847, 100000100848, 100000100849, 100000100850, 100000100851, 100000100852, 100000100853, 100000100854, 100000100855, 100000100856, 100000100857, 100000100858, 100000100859, 100000100860, 100000100861, 100000100862, 100000100863, 100000100864, 100000100865, 100000100866, 100000100867, 100000100868, 100000100869, 100000100870, 10000

In [35]:
'''
print(config["batch_size"])
for batch in train_loader:
    X, targets, padding_masks, IDs = batch
    print(X.shape)
    print(X[0])
    print(X.dtype)
    print("-"*20)
    print(targets.shape)
    print(targets[0])
    print(targets.dtype)
    print("-"*20)
    print(padding_masks.shape)
    print(padding_masks[0])
    print("-"*20)
    print(IDs)
    break
'''

'\nprint(config["batch_size"])\nfor batch in train_loader:\n    X, targets, padding_masks, IDs = batch\n    print(X.shape)\n    print(X[0])\n    print(X.dtype)\n    print("-"*20)\n    print(targets.shape)\n    print(targets[0])\n    print(targets.dtype)\n    print("-"*20)\n    print(padding_masks.shape)\n    print(padding_masks[0])\n    print("-"*20)\n    print(IDs)\n    break\n'

# Evaluate on validation before training

In [36]:
aggr_metrics_val, best_metrics, best_value = validate(val_evaluator, tensorboard_writer, config, best_metrics,
                                                      best_value, epoch=0)
metrics_names, metrics_values = zip(*aggr_metrics_val.items())
metrics.append(list(metrics_values))

2023-05-11 13:52:16,070 | INFO : Evaluating on validation set ...


Evaluating Epoch 0   0.0% | batch:         0 of       173	|	loss: 12.0479
Evaluating Epoch 0   0.6% | batch:         1 of       173	|	loss: 6.54869
Evaluating Epoch 0   1.2% | batch:         2 of       173	|	loss: 2.20177
Evaluating Epoch 0   1.7% | batch:         3 of       173	|	loss: 14.2715
Evaluating Epoch 0   2.3% | batch:         4 of       173	|	loss: 2.55974
Evaluating Epoch 0   2.9% | batch:         5 of       173	|	loss: 10.1805
Evaluating Epoch 0   3.5% | batch:         6 of       173	|	loss: 2.71987
Evaluating Epoch 0   4.0% | batch:         7 of       173	|	loss: 13.9272
Evaluating Epoch 0   4.6% | batch:         8 of       173	|	loss: 1.8422
Evaluating Epoch 0   5.2% | batch:         9 of       173	|	loss: 11.6545
Evaluating Epoch 0   5.8% | batch:        10 of       173	|	loss: 5.5449
Evaluating Epoch 0   6.4% | batch:        11 of       173	|	loss: 7.54886
Evaluating Epoch 0   6.9% | batch:        12 of       173	|	loss: 3.79315
Evaluating Epoch 0   7.5% | batch:      

Evaluating Epoch 0  71.7% | batch:       124 of       173	|	loss: 98.9451
Evaluating Epoch 0  72.3% | batch:       125 of       173	|	loss: 196.639
Evaluating Epoch 0  72.8% | batch:       126 of       173	|	loss: 7.32635
Evaluating Epoch 0  73.4% | batch:       127 of       173	|	loss: 3.07852
Evaluating Epoch 0  74.0% | batch:       128 of       173	|	loss: 10.8799
Evaluating Epoch 0  74.6% | batch:       129 of       173	|	loss: 47.5816
Evaluating Epoch 0  75.1% | batch:       130 of       173	|	loss: 14.222
Evaluating Epoch 0  75.7% | batch:       131 of       173	|	loss: 8.23271
Evaluating Epoch 0  76.3% | batch:       132 of       173	|	loss: 12.3051
Evaluating Epoch 0  76.9% | batch:       133 of       173	|	loss: 65.8668
Evaluating Epoch 0  77.5% | batch:       134 of       173	|	loss: 34.5467
Evaluating Epoch 0  78.0% | batch:       135 of       173	|	loss: 132.673
Evaluating Epoch 0  78.6% | batch:       136 of       173	|	loss: 23.4484
Evaluating Epoch 0  79.2% | batch:     

2023-05-11 13:52:18,859 | INFO : Validation runtime: 0.0 hours, 0.0 minutes, 2.787672519683838 seconds

2023-05-11 13:52:18,859 | INFO : Avg val. time: 0.0 hours, 0.0 minutes, 2.787672519683838 seconds
2023-05-11 13:52:18,859 | INFO : Avg batch val. time: 0.01611371398661178 seconds
2023-05-11 13:52:18,860 | INFO : Avg sample val. time: 0.00012599649806480624 seconds
2023-05-11 13:52:18,860 | INFO : Epoch 0 Validation Summary: epoch: 0.000000 | loss: 39.687664 | 


Evaluating Epoch 0  92.5% | batch:       160 of       173	|	loss: 150.464
Evaluating Epoch 0  93.1% | batch:       161 of       173	|	loss: 219.855
Evaluating Epoch 0  93.6% | batch:       162 of       173	|	loss: 291.742
Evaluating Epoch 0  94.2% | batch:       163 of       173	|	loss: 145.166
Evaluating Epoch 0  94.8% | batch:       164 of       173	|	loss: 172.257
Evaluating Epoch 0  95.4% | batch:       165 of       173	|	loss: 217.625
Evaluating Epoch 0  96.0% | batch:       166 of       173	|	loss: 91.7848
Evaluating Epoch 0  96.5% | batch:       167 of       173	|	loss: 177.566
Evaluating Epoch 0  97.1% | batch:       168 of       173	|	loss: 161.639
Evaluating Epoch 0  97.7% | batch:       169 of       173	|	loss: 101.492
Evaluating Epoch 0  98.3% | batch:       170 of       173	|	loss: 228.358
Evaluating Epoch 0  98.8% | batch:       171 of       173	|	loss: 130.298
Evaluating Epoch 0  99.4% | batch:       172 of       173	|	loss: 140.249



/home/tianyi/anaconda3/envs/transformer/lib/python3.8/site-packages/numpy/lib/npyio.py:713: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.
  val = np.asanyarray(val)


# Starting training...

In [37]:
logger.info('Starting training...')
for epoch in tqdm(range(start_epoch + 1, config["epochs"] + 1), desc='Training Epoch', leave=False):
    mark = epoch if config['save_all'] else 'last'
    epoch_start_time = time.time()
    # Training
    aggr_metrics_train = trainer.train_epoch(epoch)  # dictionary of aggregate epoch metrics
    epoch_runtime = time.time() - epoch_start_time
    print()
    print_str = 'Epoch {} Training Summary: '.format(epoch)
    for k, v in aggr_metrics_train.items():
        tensorboard_writer.add_scalar('{}/train'.format(k), v, epoch)
        print_str += '{}: {:8f} | '.format(k, v)
    logger.info(print_str)
    logger.info("Epoch runtime: {} hours, {} minutes, {} seconds\n".format(*utils.readable_time(epoch_runtime)))
    total_epoch_time += epoch_runtime
    avg_epoch_time = total_epoch_time / (epoch - start_epoch)
    avg_batch_time = avg_epoch_time / len(train_loader)
    avg_sample_time = avg_epoch_time / len(train_dataset)
    logger.info("Avg epoch train. time: {} hours, {} minutes, {} seconds".format(*utils.readable_time(avg_epoch_time)))
    logger.info("Avg batch train. time: {} seconds".format(avg_batch_time))
    logger.info("Avg sample train. time: {} seconds".format(avg_sample_time))

    # evaluate if first or last epoch or at specified interval
    if (epoch == config["epochs"]) or (epoch == start_epoch + 1) or (epoch % config['val_interval'] == 0):
        aggr_metrics_val, best_metrics, best_value = validate(val_evaluator, tensorboard_writer, config,
                                                              best_metrics, best_value, epoch)
        metrics_names, metrics_values = zip(*aggr_metrics_val.items())
        metrics.append(list(metrics_values))

    utils.save_model(os.path.join(config['save_dir'], 'model_{}.pth'.format(mark)), epoch, model, optimizer)

    # Learning rate scheduling
    if epoch == config['lr_step'][lr_step]:
        utils.save_model(os.path.join(config['save_dir'], 'model_{}.pth'.format(epoch)), epoch, model, optimizer)
        lr = lr * config['lr_factor'][lr_step]
        if lr_step < len(config['lr_step']) - 1:  # so that this index does not get out of bounds
            lr_step += 1
        logger.info('Learning rate updated to: ', lr)
        for param_group in optimizer.param_groups:
            param_group['lr'] = lr

    # Difficulty scheduling
    if config['harden'] and check_progress(epoch):
        train_loader.dataset.update()
        val_loader.dataset.update()


2023-05-11 13:52:18,902 | INFO : Starting training...


Training Epoch:   0%|          | 0/50 [00:00<?, ?it/s]

/home/tianyi/Documents/mvts_transformer/src/optimizers.py:69: UserWarning: This overload of addcmul_ is deprecated:
	addcmul_(Number value, Tensor tensor1, Tensor tensor2)
Consider using one of the following signatures instead:
	addcmul_(Tensor tensor1, Tensor tensor2, *, Number value) (Triggered internally at /opt/conda/conda-bld/pytorch_1670525541702/work/torch/csrc/utils/python_arg_parser.cpp:1420.)
  exp_avg_sq.mul_(beta2).addcmul_(1 - beta2, grad, grad)


Training Epoch 1   0.0% | batch:         0 of       691	|	loss: 0.208358
Training Epoch 1   0.1% | batch:         1 of       691	|	loss: 0.320449
Training Epoch 1   0.3% | batch:         2 of       691	|	loss: 0.230403
Training Epoch 1   0.4% | batch:         3 of       691	|	loss: 0.355896
Training Epoch 1   0.6% | batch:         4 of       691	|	loss: 0.302415
Training Epoch 1   0.7% | batch:         5 of       691	|	loss: 0.268689
Training Epoch 1   0.9% | batch:         6 of       691	|	loss: 0.31703
Training Epoch 1   1.0% | batch:         7 of       691	|	loss: 0.341786
Training Epoch 1   1.2% | batch:         8 of       691	|	loss: 0.268593
Training Epoch 1   1.3% | batch:         9 of       691	|	loss: 0.299239
Training Epoch 1   1.4% | batch:        10 of       691	|	loss: 0.278805
Training Epoch 1   1.6% | batch:        11 of       691	|	loss: 0.362612
Training Epoch 1   1.7% | batch:        12 of       691	|	loss: 0.28584
Training Epoch 1   1.9% | batch:        13 of       6

Training Epoch 1  16.8% | batch:       116 of       691	|	loss: 0.0515195
Training Epoch 1  16.9% | batch:       117 of       691	|	loss: 0.0298781
Training Epoch 1  17.1% | batch:       118 of       691	|	loss: 0.0494716
Training Epoch 1  17.2% | batch:       119 of       691	|	loss: 0.0363062
Training Epoch 1  17.4% | batch:       120 of       691	|	loss: 0.0542892
Training Epoch 1  17.5% | batch:       121 of       691	|	loss: 0.0356214
Training Epoch 1  17.7% | batch:       122 of       691	|	loss: 0.0519145
Training Epoch 1  17.8% | batch:       123 of       691	|	loss: 0.0453364
Training Epoch 1  17.9% | batch:       124 of       691	|	loss: 0.04807
Training Epoch 1  18.1% | batch:       125 of       691	|	loss: 0.049525
Training Epoch 1  18.2% | batch:       126 of       691	|	loss: 0.0528179
Training Epoch 1  18.4% | batch:       127 of       691	|	loss: 0.042487
Training Epoch 1  18.5% | batch:       128 of       691	|	loss: 0.0531378
Training Epoch 1  18.7% | batch:       129

...

2023-05-11 14:04:19,945 | INFO : Epoch 50 Training Summary: epoch: 50.000000 | loss: 0.000059 | 
2023-05-11 14:04:19,946 | INFO : Epoch runtime: 0.0 hours, 0.0 minutes, 13.331368923187256 seconds

2023-05-11 14:04:19,947 | INFO : Avg epoch train. time: 0.0 hours, 0.0 minutes, 13.360761766433717 seconds
2023-05-11 14:04:19,947 | INFO : Avg batch train. time: 0.019335400530294814 seconds
2023-05-11 14:04:19,947 | INFO : Avg sample train. time: 0.00015121681587271482 seconds
2023-05-11 14:04:19,948 | INFO : Evaluating on validation set ...


Training Epoch 50  99.7% | batch:       689 of       691	|	loss: 4.85204e-05
Training Epoch 50  99.9% | batch:       690 of       691	|	loss: 0.00196019

Evaluating Epoch 50   0.0% | batch:         0 of       173	|	loss: 0.0019139
Evaluating Epoch 50   0.6% | batch:         1 of       173	|	loss: 0.00224898
Evaluating Epoch 50   1.2% | batch:         2 of       173	|	loss: 0.00144364
Evaluating Epoch 50   1.7% | batch:         3 of       173	|	loss: 0.00210102
Evaluating Epoch 50   2.3% | batch:         4 of       173	|	loss: 0.00143596
Evaluating Epoch 50   2.9% | batch:         5 of       173	|	loss: 0.00101209
Evaluating Epoch 50   3.5% | batch:         6 of       173	|	loss: 0.00153029
Evaluating Epoch 50   4.0% | batch:         7 of       173	|	loss: 0.00217094
Evaluating Epoch 50   4.6% | batch:         8 of       173	|	loss: 0.00159128
Evaluating Epoch 50   5.2% | batch:         9 of       173	|	loss: 0.00166392
Evaluating Epoch 50   5.8% | batch:        10 of       173	|	loss: 

Evaluating Epoch 50  67.6% | batch:       117 of       173	|	loss: 0.00041363
Evaluating Epoch 50  68.2% | batch:       118 of       173	|	loss: 0.000138105
Evaluating Epoch 50  68.8% | batch:       119 of       173	|	loss: 0.000277909
Evaluating Epoch 50  69.4% | batch:       120 of       173	|	loss: 0.000319128
Evaluating Epoch 50  69.9% | batch:       121 of       173	|	loss: 1.61847e-05
Evaluating Epoch 50  70.5% | batch:       122 of       173	|	loss: 6.66801e-05
Evaluating Epoch 50  71.1% | batch:       123 of       173	|	loss: 3.00269e-05
Evaluating Epoch 50  71.7% | batch:       124 of       173	|	loss: 3.98479e-05
Evaluating Epoch 50  72.3% | batch:       125 of       173	|	loss: 0.000134776
Evaluating Epoch 50  72.8% | batch:       126 of       173	|	loss: 0.000391311
Evaluating Epoch 50  73.4% | batch:       127 of       173	|	loss: 0.000413385
Evaluating Epoch 50  74.0% | batch:       128 of       173	|	loss: 0.000134788
Evaluating Epoch 50  74.6% | batch:       129 of     

2023-05-11 14:04:22,045 | INFO : Validation runtime: 0.0 hours, 0.0 minutes, 2.0966737270355225 seconds

2023-05-11 14:04:22,045 | INFO : Avg val. time: 0.0 hours, 0.0 minutes, 2.107891241709391 seconds
2023-05-11 14:04:22,045 | INFO : Avg batch val. time: 0.012184342437626538 seconds
2023-05-11 14:04:22,046 | INFO : Avg sample val. time: 9.527192052923802e-05 seconds
2023-05-11 14:04:22,047 | INFO : Epoch 50 Validation Summary: epoch: 50.000000 | loss: 0.001097 | 


Evaluating Epoch 50  97.1% | batch:       168 of       173	|	loss: 5.80356e-06
Evaluating Epoch 50  97.7% | batch:       169 of       173	|	loss: 5.61952e-06
Evaluating Epoch 50  98.3% | batch:       170 of       173	|	loss: 4.54995e-06
Evaluating Epoch 50  98.8% | batch:       171 of       173	|	loss: 3.05612e-06
Evaluating Epoch 50  99.4% | batch:       172 of       173	|	loss: 5.37267e-06



In [38]:
# Export evolution of metrics over epochs
header = metrics_names
metrics_filepath = os.path.join(config["output_dir"], "metrics_" + config["experiment_name"] + ".xls")
book = utils.export_performance_metrics(metrics_filepath, metrics, header, sheet_name="metrics")

# Export record metrics to a file accumulating records from all experiments
utils.register_record(config["records_file"], config["initial_timestamp"], config["experiment_name"],
                      best_metrics, aggr_metrics_val, comment=config['comment'])

logger.info('Best {} was {}. Other metrics: {}'.format(config['key_metric'], best_value, best_metrics))
logger.info('All Done!')

total_runtime = time.time() - total_start_time
logger.info("Total runtime: {} hours, {} minutes, {} seconds\n".format(*utils.readable_time(total_runtime)))

#return best_value
print(best_value)

2023-05-11 14:04:22,067 | INFO : Exported per epoch performance metrics in '../experiments/poseErrorPred_fromScratch_Regression_Selective_2023-05-11_13-51-42_STl/metrics_poseErrorPred_fromScratch_Regression_Selective.xls'
2023-05-11 14:04:22,072 | INFO : Exported performance record to 'Regression_records.xls'
2023-05-11 14:04:22,072 | INFO : Best loss was 0.0006208891131162728. Other metrics: OrderedDict([('epoch', 18), ('loss', 0.0006208891131162728)])
2023-05-11 14:04:22,073 | INFO : All Done!
2023-05-11 14:04:22,073 | INFO : Total runtime: 0.0 hours, 12.0 minutes, 17.043140649795532 seconds



0.0006208891131162728


In [ ]:
5*10**5